**2019 ladakh glaciers mapping**

In [ ]:
!pip install folium
!pip install earthengine-api
!pip install geopandas

In [ ]:
import geopandas as gpd
import folium
import ee

In [ ]:
# Authenticate and Initialize the Earth Engine API
ee.Authenticate()
ee.Initialize()

To authorize access needed by Earth Engine, open the following URL in a web browser and follow the instructions. If the web browser does not start automatically, please manually browse the URL below.

    https://code.earthengine.google.com/client-auth?scopes=https%3A//www.googleapis.com/auth/earthengine%20https%3A//www.googleapis.com/auth/devstorage.full_control&request_id=Sp6GDDwQ1huozlOL-pk13gPPbuJUQEhcIpL186SqAwA&tc=BR8XQPMWNsJ4sSlgnCcZmQDvlC0Bc84YI_51nlMiLaM&cc=7hRMoylKLbONa_lzZBtVZFptyh5Ljovf7Bkad1AOiUs

The authorization workflow will generate a code, which you should paste in the box below.
Enter verification code: 4/1Adeu5BXiPlY6PD9SK9baJ53wv0LlJd-RxKWCSoz76rJ742u8tnsKZUkt3YQ

Successfully saved authorization token.


In [ ]:
# Define a method to display Earth Engine image tiles on a folium map.
def add_ee_layer(self, ee_image_object, vis_params, name):
    map_id_dict = ee.Image(ee_image_object).getMapId(vis_params)
    folium.raster_layers.TileLayer(
        tiles=map_id_dict['tile_fetcher'].url_format,
        attr='Map Data &copy; Google Earth Engine',
        name=name,
        overlay=True,
        control=True
    ).add_to(self)
    # Add Earth Engine drawing method to folium.
folium.Map.add_ee_layer = add_ee_layer

# Set the center of the map
location = [34.0, 77.5]
m = folium.Map(location=location, zoom_start=7)
# Define the bounds of the rectangle for the AOI
bounds = [[32.5, 75.0], [35.0, 80.0]]


In [ ]:
# Load glacier data from GeoPackage file
glacier_files = [
    "/content/LEH_GLACIERS_2019.gpkg",
    "/content/SHAYOK_GLACIERS_2019.gpkg",
    "/content/SURU_GLACIERS_2019.gpkg",
    "/content/TSOKAR_GLACIERS_2019.gpkg",
    "/content/TSOMORIRI_GLACIERS_2019.gpkg",
    "/content/ZANSKAR_GLACIERS_2019.gpkg",
    "/content/PANGONG_GLACIERS_2019.gpkg"
]

In [ ]:
# Set the area of interest (AOI)
aoi = ee.Geometry.Rectangle([75.0, 36, 82, 32])

# Load a landsat image. Filter by date and AOI and cloud cover.
landsat = (ee.ImageCollection('LANDSAT/LC08/C01/T1_TOA')
           .filterDate(ee.Date('2019-01-01'), ee.Date('2019-12-31'))
           .filterBounds(aoi)
           .filterMetadata('CLOUD_COVER', 'less_than', 10)
           .median())  # Take the median to remove clouds

# Use normalized difference to create a glacier mask
ndwi = landsat.normalizedDifference(['B3', 'B6'])
glacier_mask = ndwi.gt(0.3)

In [ ]:
# Define visualization parameters for Landsat imagery
landsat_vis_params = {'bands': ['B4', 'B3', 'B2'], 'max': 0.3}

# Add the Landsat image and glacier mask to the map
m.add_ee_layer(landsat, landsat_vis_params, 'Landsat Image')
m.add_ee_layer(glacier_mask.updateMask(glacier_mask), {'palette': 'blue'}, 'Glacier Mask')

In [ ]:
# Loop through glacier files and add them to the map
for idx, glacier_file in enumerate(glacier_files):
    glacier_data = gpd.read_file(glacier_file)
    glacier_data['area'] = glacier_data.area
    glacier_data = glacier_data.to_crs(epsg=4326)

    # Plotting the glacier data as GeoJSON layers
    for _, r in glacier_data.iterrows():
        sim_geo = gpd.GeoSeries(r["geometry"]).simplify(tolerance=0.001)
        geo_j = sim_geo.to_json()
        geo_j = folium.GeoJson(data=geo_j)
        folium.Popup(r["JNUOAId"]).add_to(geo_j)
        geo_j.add_to(m)

In [ ]:
# Add a layer control panel to the map.
m.add_child(folium.LayerControl())
# Display the map
display(m)

